In [1]:
cd ..

D:\J.H.LEE\05. CODING\Python\Project\tdatlib


In [2]:
from tdatlib import macro, market, index, stock
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import pandas as pd

# Initialize

In [3]:
macro = macro()
market = market.KR()
index = index()

index.data.period = macro.data.period = 20

In [5]:
tickers = pd.DataFrame(
    data=[
        dict(ticker="5046",   종류="지수", 이름="KRX은행"),
        dict(ticker="091170", 종류="ETF", 이름="KODEX은행"),
        dict(ticker="091220", 종류="ETF", 이름="TIGER은행"),
        dict(ticker="105560", 종류="주식", 이름="KB금융"),
        dict(ticker="086790", 종류="주식", 이름="하나금융지주"),
        dict(ticker="139130", 종류="주식", 이름="DGB금융지주"),
        dict(ticker="055550", 종류="주식", 이름="신한지주"),
        dict(ticker="024110", 종류="주식", 이름="기업은행"),
        dict(ticker="138930", 종류="주식", 이름="BNK금융지주"),
        dict(ticker="316140", 종류="주식", 이름="우리금융지주"),
        dict(ticker="038540", 종류="주식", 이름="상상인"),
    ]
).set_index(keys='ticker').join(other=market.icm)

stock_objs = {ticker: stock.kr(ticker=ticker) for ticker in tickers[tickers.종류 == '주식'].index}

# BM & Products

- 은행 사업 구조 및 최대 매출처 확인
- 주요 매출처
  * 유가 증권 평가 및 처분 이익<br>
    : 1년 또는 1영업주기 내 현금화할 의도가 있는 증권을 유가 증권이라고 한다.<br>
    : 증권은 CD, CP 등 단기 증서 및 보통주/우선주의 주식과 사채, 어음 등 채무 증권을 말한다.<br>
    : 이러한 유가 증권을 취득 가액보다 높은 이익으로 처분할 때 발생하는 이익 및 보유 증권의 평가액을 매출에 반영한다.<br>
  * 신탁 업무 운용 수익
    : 운용

In [8]:
target = tickers.sort_values(by='시가총액', ascending=False)[:4]
fig = make_subplots(
    rows=2, cols=2,
    vertical_spacing=0.12, horizontal_spacing=0.1,
    subplot_titles=tuple(target.이름.tolist()),
    specs=[
        [{"type": "domain"}, {"type": "domain"}],
        [{"type": "domain"}, {"type": "domain"}]
    ]
)

for n, ticker in enumerate(target.index):
    obj = stock_objs[ticker]
    products = obj.fnguide.Products
    fig.add_trace(
        trace = go.Pie(
            name='Product',
            labels=products.index,
            values=products,
            visible=True,
            showlegend=True,
            automargin=True,
            textfont=dict(color='white'),
            textinfo='label+percent',
            insidetextorientation='radial',
            hoverinfo='label+percent',
        ), row = n // 2 + 1, col = n % 2 + 1
    )

fig.update_layout(    
    title=f'<b>은행주</b> 주요 매출',
    plot_bgcolor='white',
    height=750,
    legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1.08,
        xanchor="right",
        x=0.96
    ),
)

for n, annotation in enumerate(fig['layout']['annotations']):
    annotation['x'] = 0 + 0.55 * (n % 2)
    annotation['xanchor'] = 'center'
    annotation['xref'] = 'paper'
fig.show()

# BM Verification

In [9]:
# 수신금리
receive_by_new = macro.data.ecos('121Y002') # 신규 취급액 기준
receive_by_left = macro.data.ecos('121Y013') # 잔액 기준

# 대출금리
loan_by_new = macro.data.ecos('121Y006') # 신규 취급액 기준
loan_by_left = macro.data.ecos('121Y015') # 잔액 기준

ValueError: cannot reindex on an axis with duplicate labels

# Macro-Relation

## 공용 데이터

In [32]:
# KRX 은행 지수
krx_bank = index.data.bank
krx_bank_trace = go.Scatter(
    x=krx_bank.index,
    y=krx_bank.종가,
    name='KRX은행지수',
    showlegend=True,
    line=dict(
#         dash='dot',
        color='black',
        width=1
    ),
    xhoverformat='%Y/%m/%d',
    hovertemplate='%{x}<br>%{y:.2f}'
)

## 기준 금리와 KRX은행지수

In [ ]:
# 한국은행 기준금리
kr_std = macro.data.KR_IR

# 미국 기준금리
us_std = macro.data.US_IR

In [51]:
fig = make_subplots(specs=[[{"secondary_y": True}]])

fig.add_trace(trace=krx_bank_trace, secondary_y=False)
fig.add_trace(
    go.Scatter(
        x=kr_std.index,
        y=kr_std,
        name='한국기준금리',
        showlegend=True,
        line_width=1.2,
        xhoverformat='%Y/%m/%d',
        hovertemplate='%{x}<br>%{y:.2f}%'
    ), secondary_y=True
)
fig.add_trace(
    go.Scatter(
        x=us_std.index,
        y=us_std,
        name='미국기준금리',
        showlegend=True,
        line_width=1.2,
        xhoverformat='%Y/%m/%d',
        hovertemplate='%{x}<br>%{y:.2f}%'
    ), secondary_y=True
)

fig.update_layout(
    title=f'<b>KRX은행지수</b>와 기준 금리 상관 관계',
    plot_bgcolor='white',
    height=750,
    legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1.08,
        xanchor="right",
        x=0.96
    ),
    xaxis=dict(
        title='날짜',
        showticklabels=True,
        showgrid=True,
        gridcolor='lightgrey'
    ),
    yaxis=dict(
        title='지수',
        showticklabels=True,
        showgrid=True,
        gridcolor='lightgrey'
    ),
    yaxis2=dict(
        title='이율[%]',
        showticklabels=True
    )
)

## 10년물 금리와 KRX은행지수

In [ ]:
# 한국채 10년물 금리
kr_10yt = macro.data.KR_10Y_TY

# 미국채 10년물 금리
us_10yt = macro.data.US_10Y_TY

In [50]:
fig = make_subplots(specs=[[{"secondary_y": True}]])

fig.add_trace(trace=krx_bank_trace, secondary_y=False)
fig.add_trace(
    go.Scatter(
        x=kr_10yt.index,
        y=kr_10yt,
        name='한국국고채10년물',
        showlegend=True,
        line_width=1.2,
        xhoverformat='%Y/%m/%d',
        hovertemplate='%{x}<br>%{y:.2f}%'
    ), secondary_y=True
)
fig.add_trace(
    go.Scatter(
        x=us_10yt.index,
        y=us_10yt,
        name='미국국고채10년물',
        showlegend=True,
        line_width=1.2,
        xhoverformat='%Y/%m/%d',
        hovertemplate='%{x}<br>%{y:.2f}%'
    ), secondary_y=True
)

fig.update_layout(
    title=f'<b>KRX은행지수</b>와 국고채10년물 상관 관계',
    plot_bgcolor='white',
    height=750,
    legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1.08,
        xanchor="right",
        x=0.96
    ),
    xaxis=dict(
        title='날짜',
        showticklabels=True,
        showgrid=True,
        gridcolor='lightgrey'
    ),
    yaxis=dict(
        title='지수',
        showticklabels=True,
        showgrid=True,
        gridcolor='lightgrey'
    ),
    yaxis2=dict(
        title='이율[%]',
        showticklabels=True
    )
)

## 원-달러 환율과 KRX은행지수

In [ ]:
# 원-달러 환율
exchange = macro.data.KRW_USD_exchange
print(f"원-달러 환율 정보:\n{exchange.columns.to_list()}\n")

In [53]:
fig = make_subplots(specs=[[{"secondary_y": True}]])

fig.add_trace(trace=krx_bank_trace, secondary_y=False)
fig.add_trace(
    go.Candlestick(
        name='원-달러 환율',
        x=exchange.index,
        open=exchange.시가,
        high=exchange.고가,
        low=exchange.저가,
        close=exchange.종가,
        visible=True,
        showlegend=True,
        increasing_line=dict(color='red'),
        decreasing_line=dict(color='royalblue'),
        xhoverformat='%Y/%m/%d',
        yhoverformat='.2f',
    ), secondary_y=True
)

fig.update_layout(
    title=f'<b>KRX은행지수</b>와 원-달러 환율',
    plot_bgcolor='white',
    height=750,
    legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1.08,
        xanchor="right",
        x=0.96
    ),
    xaxis=dict(
        title='날짜',
        showticklabels=True,
        showgrid=True,
        gridcolor='lightgrey',
    ),
    yaxis=dict(
        title='지수',
        showticklabels=True,
        showgrid=True,
        gridcolor='lightgrey'
    ),
    yaxis2=dict(
        title='KRW',
        showticklabels=True
    ),
    xaxis_rangeslider=dict(visible=False)
)

* 습작 노트

In [ ]:
# 금리 정보
kr_interests = macro.data.ecos('722Y001')
print(f"한국은행 금리정보:\n{kr_interests.columns.to_list()}\n")

In [17]:
deposit = kr_interests['자금조정 예금금리'].dropna().astype(float)
# loan = kr_interests['자금조정 대출금리'].dropna().astype(float)
loan = kr_interests['정부대출금금리'].dropna().astype(float)
margin = loan - deposit

fig = go.Figure()

fig.add_trace(
    go.Scatter(
        x=deposit.index,
        y=deposit,
        name='예금금리',
    )
)
fig.add_trace(
    go.Scatter(
        x=loan.index,
        y=loan,
        name='대출금리'
    )
)
fig.add_trace(
    go.Scatter(
        x=margin.index,
        y=margin,
        name='예대마진'
    )
)
